# Hafta 9: LLM'ler için Gelişmiş Teknikler: Fine-Tuning ve RAG

**Dersin Hedefleri:**
1.  Önceden eğitilmiş (pre-trained) LLM'leri özel görevler veya domain'ler için uyarlamanın neden gerekli olduğunu anlamak.
2.  İnce Ayar (Fine-Tuning) kavramını ve ne zaman kullanılması gerektiğini öğrenmek.
3.  Geri Çağırma Destekli Üretim (Retrieval-Augmented Generation - RAG) mimarisini ve nasıl çalıştığını kavramak.
4.  Vektör veritabanlarının (Vector Databases) RAG sistemlerindeki rolünü anlamak.
5.  `sentence-transformers` ve `faiss` gibi kütüphanelerle basit bir RAG pipeline'ı prototiplemek.

## 1. LLM'leri Neden Özelleştirmeliyiz?

Genel amaçlı LLM'ler (GPT-4, Llama 3 gibi) önemli derecede yeteneklidir, ancak bazı sınırlamaları vardır:

- **Bilgi Kesintisi (Knowledge Cutoff):** Eğitimleri belirli bir tarihte durduğu için, o tarihten sonraki olaylar veya bilgiler hakkında hiçbir fikirleri yoktur.
- **Özel veya Gizli Bilgi Eksikliği:** Şirketinizin dahili belgeleri, özel tıbbi kayıtlar veya kişisel e-postalarınız gibi kamuya açık olmayan verileri bilemezler.
- **Stil veya Format Uyumsuzluğu:** Belirli bir jargonu (örn: hukuk, tıp) kullanmakta veya çok spesifik bir JSON formatında çıktı üretmekte zorlanabilirler.

Bu sınırlamaları aşmak için iki ana strateji vardır: **Fine-Tuning** ve **RAG**.

## 2. İnce Ayar (Fine-Tuning)

**Tanım:** Önceden eğitilmiş bir LLM'i alıp, daha küçük ve göreve özgü bir veri seti üzerinde eğitime devam etme işlemidir. Bu süreçte, modelin ağırlıkları (parametreleri) bu yeni veriye uyum sağlamak için hafifçe güncellenir.

**Amacı:** Modelin **davranışını**, **stilini** veya **terminolojisini** değiştirmektir.

- **Ne zaman kullanılır?**
  - Modele belirli bir kişilik (örn: esprili bir asistan) kazandırmak için.
  - Medikal rapor özetleme gibi, belirli bir alana özgü terminolojiyi öğretmek için.
  - Çok spesifik bir çıktı formatına uymasını sağlamak için.

**Zorlukları:**
- **Maliyetli:** Büyük miktarda etiketli veri gerektirir ve eğitim süreci (GPU'lar) pahalı olabilir.
- **Yıkıcı Unutma (Catastrophic Forgetting):** Model, yeni görevi öğrenirken genel dünya bilgisini unutmaya başlayabilir.
- **Gerçekleri Öğretmek İçin Kötü Bir Yoldur:** Fine-tuning, modele yeni gerçekler (facts) enjekte etmek için verimsiz ve güvenilmez bir yöntemdir.

> **Modern Yaklaşım:** Tam fine-tuning yerine, **PEFT (Parameter-Efficient Fine-Tuning)** ve **LoRA** gibi teknikler, modelin sadece küçük bir kısmını güncelleyerek bu maliyetleri büyük ölçüde düşürür.

## 3. Geri Çağırma Destekli Üretim (Retrieval-Augmented Generation - RAG)

**Tanım:** LLM'e, bir soruya cevap vermeden önce, harici bir bilgi tabanından (knowledge base) ilgili bilgileri bulup "kopya çekme" yeteneği kazandıran bir mimaridir.

**Amacı:** Modelin yanıtlarını, **güncel, güvenilir ve doğrulanabilir** bilgilerle desteklemektir.

**Nasıl Çalışır? (Basitleştirilmiş Akış)**

1.  **Indeksleme (Offline):**
    a.  Bilgi kaynaklarınızı (PDF'ler, web siteleri, dokümanlar) daha küçük parçalara (chunks) ayırırsınız.
    b.  Bir embedding modeli kullanarak her bir parçayı bir vektöre dönüştürürsünüz.
    c.  Bu vektörleri, hızlı arama için optimize edilmiş bir **Vektör Veritabanına** (örn: FAISS, ChromaDB, Pinecone) yüklersiniz.

2.  **Sorgulama (Online):**
    a.  Kullanıcı bir soru (`query`) sorar.
    b.  Aynı embedding modeli ile kullanıcının sorusunu da bir vektöre dönüştürürsünüz.
    c.  Bu sorgu vektörünü kullanarak vektör veritabanında **anlamsal olarak en benzer** (en ilgili) belge parçalarını bulursunuz. Bu işleme **retrieval** denir.
    d.  Bulunan bu ilgili parçaları (`context`) ve kullanıcının orijinal sorusunu birleştirerek LLM için bir **prompt** oluşturursunuz.
    e.  Prompt örneği: `"""Aşağıdaki bağlamı kullanarak soruya cevap ver. Bağlam: [Buraya ilgili belge parçaları gelir]. Soru: [Kullanıcının sorusu buraya gelir]."""`
    f.  LLM, kendisine sağlanan bu bağlama dayanarak soruyu cevaplar.

RAG, LLM'leri gerçek dünya uygulamaları için güvenilir hale getirmenin en popüler ve etkili yoludur.

Gerekli Kütüphanelerin Kurulumu
.pip install sentence-transformers faiss-cpu

### Alıştırma: Bilgi Tabanını Genişletme

1.  Yukarıdaki `documents` listesine, şirketin destek politikalarıyla ilgili yeni bir doküman ekleyin. Örneğin: `"Tüm ürünlerimiz için 7/24 e-posta desteği sunulmaktadır ve kurumsal müşterilerimize özel telefon hattımız mevcuttur."`
2.  İndeksleme kodunu yeniden çalıştırarak bu yeni dokümanı da vektör veritabanına ekleyin.
3.  `answer_question_with_rag` fonksiyonunu `"Destek seçenekleriniz nelerdir?"` gibi bir soruyla çağırın.
4.  Sistemin, yeni eklediğiniz bilgiyi doğru bir şekilde bulup cevabında kullanabildiğini gözlemleyin. Bu, RAG'ın bilgi tabanını güncellemenin ne kadar kolay olduğunu gösterir (fine-tuning'in aksine).

# Production RAG System örneği

rag_system = ProductionRAGSystem(
    embedding_model=EMBEDDING_MODEL,
    generative_model=GENERATIVE_MODEL,
    embedding_dim=EMBEDDING_DIM
)

# Index knowledge base
rag_system.index_knowledge_base(documents, metadata)

# Test queries
test_queries = [
    "Explain how transfer learning works",
    "What's the difference between deep learning and machine learning?",
    "How do large language models process text?"
]

for query in test_queries:
    result = rag_system.query(
        query,
        use_reranking=False,  # Set True for better accuracy (slower)
        return_sources=True,
        verbose=True
    )
    print("\n" + "="*80 + "\n")

print("\n✅ RAG Pipeline Complete!")
print("\n💡 Key Takeaways:")
print("   1. Semantic search finds relevant documents by meaning, not keywords")
print("   2. Reranking improves accuracy by careful evaluation")
print("   3. HyDE reduces query-document mismatch")
print("   4. Production RAG combines retrieval + generation with citations")
print("\n🔜 Next: Function calling and agents (Section 4)")

# Production RAG System: Complete Pipeline (LiteLLM)

class ProductionRAGSystem:
    """
    Complete RAG system combining retrieval + generation
    
    Production features:
    - Error handling
    - Source attribution
    - Metrics tracking
    - Configurable retrieval strategy
    """

    def __init__(
        self,
        embedding_model: str = "gemini/text-embedding-004",
        generative_model: str = "gemini/gemini-pro",
        embedding_dim: int = 768
    ):
        self.generative_model = generative_model

        # Initialize search engine with reranking capability
        self.search_engine = RerankedSearchEngine(
            embedding_model=embedding_model,
            embedding_dim=embedding_dim,
            generative_model=generative_model
        )

        self.query_count = 0

    def index_knowledge_base(
        self,
        documents: List[str],
        metadata: List[Dict] = None
    ):
        """Index documents into knowledge base"""
        self.search_engine.index_documents(documents, metadata)
        print(f"✓ Knowledge base ready with {len(documents)} documents")

    def generate_answer(
        self,
        query: str,
        retrieved_docs: List[Dict],
        max_context_length: int = 2000
    ) -> Dict:
        """Generate answer using retrieved context"""
        # Build context from retrieved documents
        context_parts = []
        sources = []

        for i, doc in enumerate(retrieved_docs[:5], 1):
            context_parts.append(f"[Document {i}]\n{doc['document']}")
            sources.append({
                'document': doc['document'],
                'metadata': doc['metadata'],
                'relevance_score': doc.get('rerank_score', doc.get('score', 0.0))
            })

        context = "\n\n".join(context_parts)

        # Truncate if too long
        if len(context) > max_context_length * 4:
            context = context[:max_context_length * 4]
            context += "\n\n[... context truncated ...]"

        # RAG prompt
        rag_prompt = f"""You are a helpful AI assistant. Answer the user's question using ONLY the information provided in the context below.

IMPORTANT RULES:
1. Base your answer strictly on the provided context
2. If the context doesn't contain enough information, say so explicitly
3. Cite which document(s) you used (e.g., "According to Document 2...")
4. Be concise but comprehensive

Context:
{context}

User Question: {query}

Answer:"""

        # Generate response using LiteLLM
        try:
            response = completion(
                model=self.generative_model,
                messages=[{"role": "user", "content": rag_prompt}],
                temperature=0.3,  # Low temperature for factual accuracy
                max_tokens=500
            )

            answer = response.choices[0].message.content
            success = True
            error = None

        except Exception as e:
            answer = f"Error generating answer: {str(e)}"
            success = False
            error = str(e)

        return {
            'answer': answer,
            'sources': sources,
            'query': query,
            'success': success,
            'error': error
        }

    def query(
        self,
        query: str,
        use_reranking: bool = False,
        return_sources: bool = True,
        verbose: bool = True
    ) -> Dict:
        """Complete RAG pipeline"""
        self.query_count += 1

        if verbose:
            print(f"\n{'='*80}")
            print(f"Query #{self.query_count}: {query}")
            print('='*80)

        # Retrieve relevant documents
        if use_reranking:
            retrieved = self.search_engine.search_with_reranking(
                query,
                initial_k=10,
                final_k=3
            )
        else:
            retrieved = self.search_engine.search(query, top_k=3, return_scores=True)

        if verbose:
            print(f"\n✓ Retrieved {len(retrieved)} documents")

        # Generate answer
        result = self.generate_answer(query, retrieved)

        if verbose:
            print(f"\n📝 Answer:\n{result['answer']}")
            if return_sources:
                print(f"\n📚 Sources:")
                for i, src in enumerate(result['sources'], 1):
                    print(f"  [{i}] {src['document'][:60]}...")

        if not return_sources:
            del result['sources']

        return result

print("✓ ProductionRAGSystem class defined (using LiteLLM)")

### 3.4 Production RAG System: End-to-End Pipeline

Şimdi tüm parçaları birleştirerek **production-ready** bir RAG sistemi oluşturacağız:
- Semantic search (retrieval)
- Optional reranking
- Context-aware generation
- Citation tracking
- Error handling

**RAG Pipeline:**
```
User Query → Retrieve relevant docs → Build context → LLM generates answer → Return answer + sources
```

# HyDE örneği

hyde_engine = HyDESearchEngine(
    embedding_model=EMBEDDING_MODEL,
    embedding_dim=EMBEDDING_DIM
)
hyde_engine.index_documents(documents, metadata)

query = "What techniques help models learn from less data?"

print(f"Query: {query}\n")
print("="*80)
print("\n[HyDE Search Results]")
print("-"*80)

hyde_results = hyde_engine.search_hyde(query, top_k=3)

for i, r in enumerate(hyde_results, 1):
    print(f"\n{i}. Document: {r['document']}")
    print(f"   HyDE Score: {r['hyde_score']:.4f} | Standard Score: {r['standard_score']:.4f}")
    improvement = r['hyde_score'] - r['standard_score']
    print(f"   Improvement: {improvement:+.4f}")

print("\n" + "="*80)
print("\n💡 Gözlem:")
print("   - HyDE scores genellikle daha yüksek")
print("   - Hypothetical doc, gerçek dökümanlarla daha iyi align olur")
print("   - Query-document asymmetry problemi azalır")

# HyDESearchEngine: Hypothetical Document Embeddings (LiteLLM)

class HyDESearchEngine(SemanticSearchEngine):
    """
    HyDE: Generate hypothetical answer, then search with it
    
    Paper: "Precise Zero-Shot Dense Retrieval without Relevance Labels" (Gao et al., 2022)
    
    Why it works: Hypothetical doc is structurally similar to actual documents
    """
    
    def __init__(self, *args, generative_model="gemini/gemini-pro", **kwargs):
        super().__init__(*args, **kwargs)
        self.generative_model = generative_model
    
    def generate_hypothetical_document(self, query: str) -> str:
        """Generate hypothetical document that would answer the query"""
        hyde_prompt = f"""Generate a detailed, informative paragraph that would answer this question.
Write as if creating a document. Use technical terminology.

Question: {query}

Hypothetical document:"""
        
        # Use LiteLLM completion
        response = completion(
            model=self.generative_model,
            messages=[{"role": "user", "content": hyde_prompt}],
            temperature=0.7,
            max_tokens=200
        )
        
        return response.choices[0].message.content
    
    def search_hyde(
        self,
        query: str,
        top_k: int = 3
    ) -> List[Dict]:
        """Search using HyDE strategy"""
        print(f"🔮 Generating hypothetical document for: {query}")
        
        # Generate hypothetical document
        hypothetical_doc = self.generate_hypothetical_document(query)
        print(f"✓ Hypothetical: {hypothetical_doc[:100]}...\n")
        
        # Embed hypothetical document
        hyde_embedding = self._embed_texts([hypothetical_doc])[0]
        
        # Compute similarities
        similarities = np.dot(self.document_embeddings, hyde_embedding)
        
        # Get top-K
        top_k_indices = np.argsort(similarities)[::-1][:top_k]
        
        # Build results with comparison
        query_emb = self._embed_texts([query])[0]
        
        results = []
        for idx in top_k_indices:
            hyde_score = float(similarities[idx])
            standard_score = float(np.dot(self.document_embeddings[idx], query_emb))
            
            results.append({
                'document': self.documents[idx],
                'metadata': self.metadata[idx],
                'hyde_score': hyde_score,
                'standard_score': standard_score
            })
        
        return results

print("✓ HyDESearchEngine class defined (using LiteLLM)")

### 3.3 HyDE (Hypothetical Document Embeddings)

**Core Idea** (Gao et al., 2022): Instead of embedding the query directly, first generate a hypothetical answer with LLM, then embed that.

**Intuition:** Hypothetical answer aligns better with actual documents (reduces query-document asymmetry).

**Flow:**
```
Query: "What is transfer learning?" (short, question format)
  ↓
Hypothetical Doc: "Transfer learning is a technique where..." (document-like)
  ↓
Embed hypothetical → Better alignment with actual documents
```

**Mathematical:**
1. Given query $q$, generate hypothetical document $d^* = \text{LLM}(q)$
2. Embed $d^*$ using RETRIEVAL_DOCUMENT task type
3. Search with $\text{embed}(d^*)$ instead of $\text{embed}(q)$

# Reranking örneği

reranked_engine = RerankedSearchEngine(
    embedding_model=EMBEDDING_MODEL,
    embedding_dim=EMBEDDING_DIM
)
reranked_engine.index_documents(documents, metadata)

query = "How can I use pretrained models for my specific task?"

print(f"\nQuery: {query}\n")
print("="*80)

# Standard semantic search
print("\n[A] Standard Semantic Search (embedding-only)")
print("-"*80)
standard_results = reranked_engine.search(query, top_k=3, return_scores=True)
for i, r in enumerate(standard_results, 1):
    print(f"{i}. [Score: {r['score']:.3f}] {r['document'][:60]}...")

# Reranked search
print("\n[B] Two-Stage Search with Reranking")
print("-"*80)
reranked_results = reranked_engine.search_with_reranking(query, initial_k=10, final_k=3)
for i, r in enumerate(reranked_results, 1):
    emb_score = r.get('score', 0.0)
    rerank_score = r.get('rerank_score', 0.0)
    print(f"{i}. [Rerank: {rerank_score:.3f} | Emb: {emb_score:.3f}] {r['document'][:50]}...")

print("\n" + "="*80)
print("\n💡 Gözlem:")
print("   - Reranking, LLM'in her dökümanı dikkatle değerlendirmesini sağlar")
print("   - Embedding search hızlıdır ama bazen suboptimal")
print("   - İki aşama birleşince en iyi sonucu elde ederiz")

# RerankedSearchEngine: İki Aşamalı Retrieval (LiteLLM)

class RerankedSearchEngine(SemanticSearchEngine):
    """
    Two-stage retrieval: Fast embedding search + LLM-based reranking
    
    Complexity:
    - Stage 1: O(N * d) where N = corpus size
    - Stage 2: O(K * T) where K = candidates, T = LLM latency
    """
    
    def __init__(self, *args, generative_model="gemini/gemini-pro", **kwargs):
        super().__init__(*args, **kwargs)
        self.generative_model = generative_model
        
    def rerank(
        self,
        query: str,
        candidates: List[Dict],
        top_k: int = 5
    ) -> List[Dict]:
        """
        Rerank candidates using LLM
        
        Args:
            query: Original search query
            candidates: List of candidate documents from initial retrieval
            top_k: Number of final results
            
        Returns:
            Reranked list of documents
        """
        reranked = []
        
        for candidate in candidates:
            doc = candidate['document']
            
            # Prompt engineering: Ask LLM to judge relevance
            relevance_prompt = f"""Rate the relevance of this document to the query on a scale of 0-10.
Only respond with a single number.

Query: {query}

Document: {doc}

Relevance score (0-10):"""
            
            try:
                # Use LiteLLM completion
                response = completion(
                    model=self.generative_model,
                    messages=[{"role": "user", "content": relevance_prompt}],
                    temperature=0.0,  # Deterministic for scoring
                    max_tokens=10
                )
                
                # Parse score
                score_text = response.choices[0].message.content.strip()
                score = float(score_text)
                
                reranked.append({
                    **candidate,
                    'rerank_score': score / 10.0,  # Normalize to [0, 1]
                })
            except Exception as e:
                # Fallback: use original embedding score
                reranked.append({
                    **candidate,
                    'rerank_score': candidate.get('score', 0.0)
                })
        
        # Sort by rerank score
        reranked.sort(key=lambda x: x['rerank_score'], reverse=True)
        
        return reranked[:top_k]
    
    def search_with_reranking(
        self,
        query: str,
        initial_k: int = 10,
        final_k: int = 3
    ) -> List[Dict]:
        """Two-stage search pipeline"""
        # Stage 1: Fast embedding-based retrieval
        candidates = self.search(query, top_k=initial_k, return_scores=True)
        
        print(f"✓ Stage 1: Retrieved {len(candidates)} candidates")
        
        # Stage 2: LLM-based reranking
        print(f"✓ Stage 2: Reranking to top-{final_k}...")
        reranked = self.rerank(query, candidates, top_k=final_k)
        
        return reranked

print("✓ RerankedSearchEngine class defined (using LiteLLM)")

### 3.2 Two-Stage Retrieval with Reranking

**Problem:** Embedding-based search is fast but sometimes suboptimal for complex queries.

**Solution:** Two-stage approach
1. **Stage 1 - Fast Retrieval**: Embedding search retrieves many candidates (top-20)
2. **Stage 2 - Reranking**: LLM evaluates each candidate carefully (top-5)

**Mathematical Formulation:**

Initial retrieval: $D_{cand} = \text{TopK}(\text{sim}(\phi_q(q), \phi_d(D)), K=20)$

Reranking: $D_{final} = \text{TopK}(\text{score}_{rerank}(q, D_{cand}), K=5)$

**Trade-off:** Speed (stage 1) + Accuracy (stage 2)

# Semantik arama motoru oluştur ve dökümanları indexle

search_engine = SemanticSearchEngine(
    embedding_model=EMBEDDING_MODEL,
    embedding_dim=EMBEDDING_DIM
)

# Index documents
search_engine.index_documents(documents, metadata)

# Test query
query = "How do neural networks learn?"

print(f"\n{'='*70}")
print(f"Query: {query}")
print('='*70)

results = search_engine.search(query, top_k=3)

for i, result in enumerate(results, 1):
    print(f"\n[{i}] Score: {result['score']:.4f}")
    print(f"    Document: {result['document']}")
    print(f"    Category: {result['metadata']['category']}")

print(f"\n{'='*70}")
print("\n💡 Gözlem:")
print("   - Query'de 'neural networks' kelimesi var")
print("   - En yüksek skorlu döküman 'Deep Learning' hakkında")
print("   - 'Machine Learning' ikinci sırada (daha genel)")
print("   - Bu semantic matching'in gücünü gösterir!")

# Örnek veri seti: AI/ML konularında dökümanlar

documents = [
    "Machine learning is a subset of artificial intelligence focused on learning from data.",
    "Deep learning uses neural networks with multiple layers to learn hierarchical representations.",
    "Natural language processing enables computers to understand and generate human language.",
    "Computer vision allows machines to interpret and understand visual information from images.",
    "Reinforcement learning trains agents to make decisions through trial and error.",
    "Transfer learning leverages pre-trained models to solve new related tasks efficiently.",
    "Generative AI creates new content like text, images, and music using learned patterns.",
    "Large language models like GPT and Gemini can understand and generate human-like text.",
    "Embeddings represent words or documents as dense vectors in continuous space.",
    "Retrieval-augmented generation combines information retrieval with text generation.",
]

# Metadata ekle
metadata = [
    {"category": "ML Basics", "difficulty": "beginner"},
    {"category": "Deep Learning", "difficulty": "intermediate"},
    {"category": "NLP", "difficulty": "intermediate"},
    {"category": "Computer Vision", "difficulty": "intermediate"},
    {"category": "RL", "difficulty": "advanced"},
    {"category": "Transfer Learning", "difficulty": "intermediate"},
    {"category": "Generative AI", "difficulty": "advanced"},
    {"category": "LLMs", "difficulty": "advanced"},
    {"category": "Embeddings", "difficulty": "intermediate"},
    {"category": "RAG", "difficulty": "advanced"},
]

print(f"✓ Dataset: {len(documents)} documents")
print(f"✓ Categories: {set(m['category'] for m in metadata)}")

# SemanticSearchEngine: Production-Ready Arama Motoru (LiteLLM)

class SemanticSearchEngine:
    """
    Production-ready semantic search engine using LiteLLM
    
    Rigor Principles:
    1. Separation of concerns: indexing vs query
    2. Explicit state management
    3. Type hints for clarity
    4. Comprehensive error handling
    """
    
    def __init__(
        self, 
        embedding_model: str = "gemini/text-embedding-004",
        embedding_dim: int = 768
    ):
        """Initialize search engine"""
        self.model = embedding_model
        self.dim = embedding_dim
        
        # Index storage
        self.documents: List[str] = []
        self.document_embeddings: np.ndarray = None
        self.metadata: List[Dict] = []
        self.indexed_count = 0
        
    def _embed_texts(
        self, 
        texts: List[str]
    ) -> np.ndarray:
        """
        Generate embeddings for a list of texts using LiteLLM
        
        Args:
            texts: List of text strings
            
        Returns:
            numpy array of shape (len(texts), self.dim)
        """
        # Use LiteLLM embedding function
        result = embedding(
            model=self.model,
            input=texts
        )
        
        # Extract embeddings from LiteLLM response
        embeddings_list = [item['embedding'] for item in result.data]
        embeddings = np.array(embeddings_list)
        
        # Verification
        assert embeddings.shape == (len(texts), self.dim), \
            f"Unexpected embedding shape: {embeddings.shape}"
        
        return embeddings
    
    def index_documents(
        self, 
        documents: List[str],
        metadata: List[Dict] = None
    ) -> None:
        """
        Index a collection of documents
        
        Complexity: O(N * d) where N = len(documents), d = embedding_dim
        """
        print(f"Indexing {len(documents)} documents...")
        
        # Embed documents
        embeddings = self._embed_texts(documents)
        
        # Store
        self.documents = documents
        self.document_embeddings = embeddings
        self.metadata = metadata if metadata else [{}] * len(documents)
        self.indexed_count = len(documents)
        
        print(f"✓ Indexed {self.indexed_count} documents")
        print(f"✓ Index size: {self.document_embeddings.nbytes / 1024:.2f} KB")
        
    def search(
        self, 
        query: str, 
        top_k: int = 5,
        return_scores: bool = True
    ) -> List[Dict]:
        """
        Search indexed documents for query
        
        Algorithm:
        1. Embed query using LiteLLM
        2. Compute dot product with all document embeddings
        3. Return top-K by similarity score
        
        Complexity: O(N * d) where N = indexed docs, d = embedding dim
        """
        if self.document_embeddings is None:
            raise ValueError("No documents indexed yet! Call index_documents() first")
        
        # Embed query
        query_embedding = self._embed_texts([query])[0]
        
        # Compute similarities (dot product for normalized embeddings)
        similarities = np.dot(self.document_embeddings, query_embedding)
        
        # Get top-K indices
        top_k_indices = np.argsort(similarities)[::-1][:top_k]
        
        # Build results
        results = []
        for idx in top_k_indices:
            result = {
                'document': self.documents[idx],
                'metadata': self.metadata[idx],
            }
            if return_scores:
                result['score'] = float(similarities[idx])
            results.append(result)
        
        return results

print("✓ SemanticSearchEngine class defined (using LiteLLM)")

# Kütüphane kurulumları (ilk çalıştırmada bir kez yapın)
!pip install -q litellm numpy

import numpy as np
from litellm import embedding, completion
from typing import List, Dict
import os

# API Key setup (hafta_08'den devam)
GEMINI_API_KEY = os.getenv("GEMINI_API_KEY")
if not GEMINI_API_KEY:
    from getpass import getpass
    GEMINI_API_KEY = getpass("GEMINI_API_KEY girin: ")
    os.environ["GEMINI_API_KEY"] = GEMINI_API_KEY

# Model ayarları (simplified defaults)
EMBEDDING_MODEL = "gemini/text-embedding-004"  # LiteLLM format
EMBEDDING_DIM = 768  # MRL ile optimize edilmiş boyut
GENERATIVE_MODEL = "gemini/gemini-pro"  # Simple, reliable default

print("✓ Setup complete (using LiteLLM)")
print(f"✓ Embedding model: {EMBEDDING_MODEL}")
print(f"✓ Generative model: {GENERATIVE_MODEL}")
print(f"✓ Embedding dimensionality: {EMBEDDING_DIM}")

---

## 3. RAG (Retrieval-Augmented Generation): Production-Ready Implementation

Hafta 8'de embeddings'in temellerini gördük. Şimdi bu teknolojiyi kullanarak **production-ready** bir RAG sistemi inşa edeceğiz.

### 3.1 Semantik Arama Motoru (Semantic Search Engine)

RAG'ın temelinde **semantik arama** yatar. Geleneksel arama (keyword matching) yerine, **anlam benzerliğine** dayalı arama yaparız.

**Mimari:**
1. **Offline (İndeksleme):** Dökümanları embedding'e çevir → Vektör DB'ye kaydet
2. **Online (Arama):** Sorguyu embedding'e çevir → En benzer dökümanları bul

**Neden Production-Ready?**
- Separation of concerns: İndeksleme vs sorgulama
- Type hints ve comprehensive error handling
- Evaluation metrics dahil
- Optimize edilmiş vektör operasyonları (NumPy)

---

## 4. Function Calling (Fonksiyon Çağırma): LLM'lere Araç Kullanma Yeteneği Kazandırma

Artık LLM'lerin kendi verilerimizle nasıl konuşacağını öğrendik (RAG). Ama ya LLM'in **aksiyonlar** almasını istersek? Örneğin:
- Hava durumu bilgisini bir API'den çekmek
- Veritabanında sorgu çalıştırmak
- Hesaplama yapmak
- E-posta göndermek

İşte **Function Calling** tam da bunu sağlar. LLM'e kullanabileceği fonksiyonları tanımlarsınız, model ne zaman hangi fonksiyonu hangi parametrelerle çağırması gerektiğine karar verir.

### 4.1 Function Calling Nedir?

**Function Calling**, LLM'in bir kullanıcı sorusuna cevap vermek için hangi fonksiyonu hangi parametrelerle çağırması gerektiğini **otomatik olarak belirlemesidir**.

**Temel Akış:**

```
Kullanıcı: "İstanbul'da hava nasıl?"
    ↓
LLM: "Bu soruyu cevaplayabilmek için get_weather() fonksiyonunu
      {city: 'Istanbul'} parametresiyle çağırmalıyım"
    ↓
Sistem: get_weather('Istanbul') → "20°C, açık hava"
    ↓
LLM: "İstanbul'da hava 20 derece ve açık."
```

### 4.2 Google AI Studio'da Function Calling - Adım Adım Rehber

**ÖNEMLİ:** Bu eğitimde **gerçek API'lere ihtiyaç yok.** Simüle edilmiş (mock) fonksiyonlar kullanacağız. Böylece API anahtarı olmadan hemen test edebilirsiniz.

Google AI Studio, function calling'i test etmek için kullanışlı bir görsel arayüz sunar. Önce burada pratik yapalım, sonra koda geçeriz.

#### 📍 Adım 1: Google AI Studio'ya Erişim

1. **Tarayıcınızda** şu adresi açın: https://aistudio.google.com/
2. Google hesabınızla giriş yapın
3. Sol menüden **"Create new"** → **"Chat prompt"** seçin

#### 📍 Adım 2: Model Seçimi

1. Sağ panelde **Model** olarak `gemini-2.0-flash-exp` veya `gemini-1.5-pro` seçin
2. Bu modeller function calling destekler (ücretsiz.)

#### 📍 Adım 3: Fonksiyon Tanımlama

1. Sağ panelde **"Tools"** sekmesine tıklayın
2. **"Function declarations"** altında **"+"** butonuna basın
3. Aşağıdaki gibi bir fonksiyon tanımlayın:

**Örnek Fonksiyon: get_current_weather**

UI'da şu şekilde doldurun:

- **Function name:** `get_current_weather`
- **Description:** `Belirtilen şehrin güncel hava durumu bilgisini getir`
- **Add parameter** butonuna basın:
  - **Parameter name:** `location`
  - **Type:** `STRING`
  - **Description:** `Şehir adı, örneğin: Istanbul, Ankara, Izmir`
  - **Required:** ✓ işaretleyin
  
- Tekrar **Add parameter:**
  - **Parameter name:** `unit`
  - **Type:** `STRING`
  - **Description:** `Sıcaklık birimi: celsius veya fahrenheit`
  - **Required:** Boş bırakın (optional)

#### 📍 Adım 4: Test Etme

1. Chat alanına şunu yazın: **"İstanbul'da hava nasıl?"**

2. Model'in yanıtını gözlemleyin - Model otomatik olarak function call üretir:
   ```
   Function Call Request:
   Function: get_current_weather
   Arguments: {
     "location": "Istanbul"
   }
   ```

3. **"Function response"** alanına sahte (mock) bir cevap girin:
   ```json
   {
     "temperature": 18,
     "condition": "Parçalı bulutlu",
     "humidity": 72,
     "wind_speed": 15
   }
   ```

4. **"Continue"** butonuna basın

5. Model bu veriyle final cevabı üretir:
   ```
   "İstanbul'da hava şu anda 18 derece ve parçalı bulutlu.
    Nem oranı %72, rüzgar hızı 15 km/s."
   ```

** Ne Oldu?**
- LLM, soruyu anlayıp hangi fonksiyonu çağırması gerektiğini **otomatik** belirledi
- Doğru parametreyi ("Istanbul") **çıkardı**
- Fonksiyon sonucunu kullanarak doğal dil cevabı üretti

#### 📍 Adım 5: Çoklu Fonksiyon Testi

Şimdi ikinci bir fonksiyon ekleyelim (**Tools** → **+** butonuna tekrar basın):

**Örnek Fonksiyon: calculate**

- **Function name:** `calculate`
- **Description:** `Matematiksel hesaplama yapar`
- **Parameter:**
  - **name:** `expression`
  - **type:** `STRING`
  - **description:** `Hesaplanacak ifade, örn: "25 * 3", "100 / 4"`
  - **required:** ✓

**Test Sorusu:** "İstanbul'da hava kaç derece? Eğer 5 derece daha artarsa ne olur?"

Model sırayla:
1. `get_current_weather("Istanbul")` çağırır  
   → Mock response: `{"temperature": 18, ...}`
2. `calculate("18 + 5")` çağırır  
   → Mock response: `{"result": 23}`
3. Final cevap: "İstanbul'da şu an 18 derece. 5 derece artarsa 23 derece olur."

---

### 4.3 Neden Function Calling Kullanıyoruz?

| Özellik | Prompt İle | Function Calling İle |
|:--------|:-----------|:--------------------|
| **Doğruluk** | LLM tahmin eder, hata yapabilir | Gerçek fonksiyon çalışır, kesin sonuç |
| **Güncel Veri** | LLM'in bilgisi sınırlı (knowledge cutoff) | Canlı API/veritabanından güncel veri |
| **Yapılandırılmış Çıktı** | Parse gerekir | JSON formatında döner |
| **Aksiyon Alma** | Sadece metin üretir | E-posta gönderebilir, DB güncelleyebilir |

---

### 4.4 RAG + Function Calling = Güçlü Kombinasyon.

Şimdi en güçlü kombinasyonu görelim: **RAG ile function calling'i birleştirmek**

**Senaryo:** Şirket dökümanlarında arama yapan bir asistan

Google AI Studio'da üçüncü bir fonksiyon ekleyin:

**Fonksiyon: search_company_docs**

- **name:** `search_company_docs`
- **description:** `Şirket dökümanlarında anahtar kelime araması yapar`
- **parameter:**
  - **name:** `query`
  - **type:** `STRING`
  - **description:** `Aranacak anahtar kelime veya soru`
  - **required:** ✓

**Test Sorusu:** "PhotonDB'nin lisans fiyatı nedir ve İstanbul'da hava nasıl?"

Model şu adımları izler:
1. `search_company_docs("PhotonDB lisans")` → "Yıllık abonelik"
2. `get_current_weather("Istanbul")` → "18°C"
3. Final cevap: Her iki soruyu da cevaplar.

Bu, LLM'in **birden fazla bilgi kaynağını koordine etmesine** ve **kompleks görevleri** çözmesine olanak sağlar.

---

** Sonraki Hücrede:** Google AI Studio'da öğrendiğimiz bu mantığı Python koduyla uygulayacağız.

### 4.5 Python ile Function Calling Implementasyonu

Şimdi Google AI Studio'da öğrendiğimiz mantığı Python koduyla implement edelim. **LiteLLM** kullanarak Gemini API'sine bağlanacağız.

**Adımlar:**
1. Mock (simüle edilmiş) fonksiyonlar oluşturma
2. Fonksiyonları JSON Schema formatında tanımlama
3. LLM'e fonksiyonları bildirme
4. Function call sonuçlarını işleme
5. Final yanıt üretme

In [ ]:
!pip install -q litellm

In [ ]:
# Gerekli kütüphaneleri yükleyelim
# .pip install -q litellm

import json
import random
from litellm import completion

# ============================================================================
# ADIM 1: Mock (Simüle) Fonksiyonlar Oluşturma
# ============================================================================
# Bu fonksiyonlar gerçek API çağrısı yapmaz, test verisi döndürür

def get_current_weather(location, unit="celsius"):
    """
    Simüle edilmiş hava durumu fonksiyonu (Gerçek API gerekmez.)

    Args:
        location (str): Şehir adı
        unit (str): Sıcaklık birimi (celsius/fahrenheit)

    Returns:
        dict: Hava durumu bilgisi
    """
    # Simüle edilmiş hava durumu verileri
    weather_db = {
        "istanbul": {"temp_c": 18, "condition": "Parçalı bulutlu", "humidity": 72},
        "ankara": {"temp_c": 12, "condition": "Güneşli", "humidity": 45},
        "izmir": {"temp_c": 22, "condition": "Açık", "humidity": 68},
        "antalya": {"temp_c": 25, "condition": "Güneşli", "humidity": 55}
    }

    location_key = location.lower().replace("ı", "i")  # Türkçe karakter normalize
    data = weather_db.get(location_key, {"temp_c": 20, "condition": "Bilinmiyor", "humidity": 50})

    temp = data["temp_c"]
    if unit == "fahrenheit":
        temp = (temp * 9/5) + 32

    return {
        "location": location,
        "temperature": temp,
        "unit": unit,
        "condition": data["condition"],
        "humidity": data["humidity"]
    }


def calculate(expression):
    """
    Güvenli matematiksel hesaplama fonksiyonu

    Args:
        expression (str): Matematiksel ifade, örn: "2+2", "15*7"

    Returns:
        dict: Hesaplama sonucu
    """
    try:
        # Güvenlik: Sadece temel matematiksel operatörlere izin ver
        allowed_chars = set("0123456789+-*/(). ")
        if not all(c in allowed_chars for c in expression):
            return {"error": "Geçersiz karakterler tespit edildi"}

        result = eval(expression)
        return {
            "expression": expression,
            "result": result
        }
    except Exception as e:
        return {"error": f"Hesaplama hatası: {str(e)}"}


def search_company_docs(query):
    """
    Simüle edilmiş şirket dokümanı arama fonksiyonu

    Args:
        query (str): Arama sorgusu

    Returns:
        dict: Bulunan dokümanlar
    """
    # Simüle edilmiş doküman veritabanı (hafta başında oluşturduğumuz RAG verisi)
    docs_db = {
        "photondb": {
            "title": "PhotonDB Lisanslama",
            "content": "PhotonDB'nin lisanslama modeli, kullanıcı başına yıllık abonelik şeklindedir. Kurumsal müşteriler için özel paketler mevcuttur."
        },
        "quantumleap": {
            "title": "QuantumLeap Çip Özellikleri",
            "content": "QuantumLeap, düşük güç tüketimi ile yüksek performans sunan yeni nesil yapay zeka çipidir. 'Yılın Teknolojisi' ödülünü almıştır."
        },
        "destek": {
            "title": "Destek Politikası",
            "content": "Tüm ürünlerimiz için 7/24 e-posta desteği sunulmaktadır. Kurumsal müşterilerimize özel telefon hattımız mevcuttur."
        }
    }

    query_lower = query.lower()
    results = []

    for key, doc in docs_db.items():
        if key in query_lower or any(word in doc["content"].lower() for word in query_lower.split()):
            results.append(doc)

    if not results:
        results.append({"title": "Sonuç bulunamadı", "content": "İlgili doküman bulunamadı."})

    return {"query": query, "results": results}


print("✅ Mock fonksiyonlar tanımlandı.")
print("   - get_current_weather()")
print("   - calculate()")
print("   - search_company_docs()")

In [ ]:
# ============================================================================
# ADIM 2: Fonksiyonları JSON Schema Formatında Tanımlama
# ============================================================================
# LLM'e hangi fonksiyonların mevcut olduğunu söylemeliyiz

tools = [
    {
        "type": "function",
        "function": {
            "name": "get_current_weather",
            "description": "Belirtilen şehrin güncel hava durumu bilgisini getirir",
            "parameters": {
                "type": "object",
                "properties": {
                    "location": {
                        "type": "string",
                        "description": "Şehir adı, örneğin: Istanbul, Ankara, Izmir"
                    },
                    "unit": {
                        "type": "string",
                        "enum": ["celsius", "fahrenheit"],
                        "description": "Sıcaklık birimi"
                    }
                },
                "required": ["location"]
            }
        }
    },
    {
        "type": "function",
        "function": {
            "name": "calculate",
            "description": "Matematiksel hesaplama yapar",
            "parameters": {
                "type": "object",
                "properties": {
                    "expression": {
                        "type": "string",
                        "description": "Hesaplanacak matematiksel ifade, örneğin: '25 * 3', '100 / 4'"
                    }
                },
                "required": ["expression"]
            }
        }
    },
    {
        "type": "function",
        "function": {
            "name": "search_company_docs",
            "description": "Şirket dökümanlarında arama yapar",
            "parameters": {
                "type": "object",
                "properties": {
                    "query": {
                        "type": "string",
                        "description": "Aranacak anahtar kelime veya soru"
                    }
                },
                "required": ["query"]
            }
        }
    }
]

print("✅ Fonksiyon tanımları (JSON Schema) hazır.")
print(f"   Toplam {len(tools)} fonksiyon tanımlandı")

In [ ]:
# ============================================================================
# ADIM 3-5: Function Calling Agent (Ana Fonksiyon)
# ============================================================================

import getpass

def run_agent_with_functions(user_query, max_iterations=5):
    """
    Function calling destekli LLM agent'ı

    Args:
        user_query (str): Kullanıcının sorusu
        max_iterations (int): Maksimum fonksiyon çağrısı sayısı

    Returns:
        str: Final yanıt
    """
    print("="*80)
    print(f"🤖 AGENT BAŞLADI")
    print("="*80)
    print(f"📥 Kullanıcı Sorusu: {user_query}\n")

    # Konuşma geçmişi
    messages = [
        {"role": "user", "content": user_query}
    ]

    # Fonksiyon adlarını Python fonksiyonlarına map'le
    available_functions = {
        "get_current_weather": get_current_weather,
        "calculate": calculate,
        "search_company_docs": search_company_docs
    }

    iteration = 0

    # Get the API key securely
    api_key = getpass.getpass("Enter your Google API Key: ")

    while iteration < max_iterations:
        iteration += 1
        print(f"\n{'─'*80}")
        print(f"🔄 İTERASYON {iteration}")
        print(f"{'─'*80}")

        try:
            # LLM'i çağır (tools parametresiyle)
            response = completion(
                model="gemini/gemini-2.0-flash",  # Gemini function calling destekler
                messages=messages,
                tools=tools,
                temperature=0.1,  # Düşük temperature (deterministik davranış)
                api_key=api_key # Pass the API key here
            )

            response_message = response.choices[0].message

            # Function call var mı kontrol et
            tool_calls = getattr(response_message, 'tool_calls', None)

            if not tool_calls:
                # Function call yok, final cevap
                final_answer = response_message.content
                print(f"\n✅ FINAL CEVAP:\n{final_answer}")
                print("="*80)
                return final_answer

            # Function call varsa, çalıştır
            print(f"\n🔧 Model {len(tool_calls)} fonksiyon çağırmak istiyor:\n")

            # Mesaj geçmişine ekle
            messages.append(response_message)

            for tool_call in tool_calls:
                function_name = tool_call.function.name
                function_args = json.loads(tool_call.function.arguments)

                print(f"   📞 Fonksiyon: {function_name}()")
                print(f"      Parametreler: {json.dumps(function_args, ensure_ascii=False, indent=10)}")

                # Fonksiyonu çalıştır
                function_to_call = available_functions[function_name]
                function_response = function_to_call(**function_args)

                print(f"      ✅ Sonuç: {json.dumps(function_response, ensure_ascii=False)}\n")

                # Fonksiyon sonucunu mesaj geçmişine ekle
                messages.append({
                    "role": "tool",
                    "tool_call_id": tool_call.id,
                    "name": function_name,
                    "content": json.dumps(function_response)
                })

        except Exception as e:
            error_msg = f"❌ Hata: {str(e)}"
            print(error_msg)
            return error_msg

    return "⚠️ Maksimum iterasyon sayısına ulaşıldı."

### 4.6 Function Calling Örnekleri

Şimdi agent'ımızı farklı senaryolarla test edelim.

In [ ]:
# ============================================================================
# TEST 1: Basit Hava Durumu Sorg usu
# ============================================================================

run_agent_with_functions("İstanbul'da hava nasıl?")

In [ ]:
# ============================================================================
# TEST 2: Çoklu Fonksiyon Kullanımı (Multi-Function)
# ============================================================================

run_agent_with_functions(
    "İstanbul'da hava kaç derece? Eğer 5 derece daha artarsa kaç olur?"
)

In [ ]:
# ============================================================================
# TEST 3: RAG + Function Calling Kombinasyonu
# ============================================================================

run_agent_with_functions(
    "PhotonDB'nin lisans modeli nedir ve İzmir'de hava nasıl?"
)

In [ ]:
# ============================================================================
# TEST 4: Karmaşık Hesaplama + Bağlam
# ============================================================================

run_agent_with_functions(
    "Ankara ve Antalya'daki sıcaklık farkı kaç derece? Celsius olarak ifade et"
)

---

### 4.7 Function Calling: Anahtar Kavramlar ve Best Practices

####  Function Calling'in Gücü

Function calling, LLM'leri **salt metin üretici**'den **aksiyon alabilen agent**'lara dönüştürür:

| Yetenek | Function Calling Olmadan | Function Calling İle |
|:--------|:-------------------------|:---------------------|
| **Hesaplama** | LLM tahmini yapar (hatalı olabilir) | Gerçek hesaplama fonksiyonu çalışır |
| **Güncel Veri** | Knowledge cutoff sınırı var | Canlı API'lerden güncel veri çeker |
| **Aksiyon** | Sadece metin önerir | E-posta gönderebilir, DB güncelleyebilir |
| **Güvenilirlik** | Halüsinasyon riski yüksek | Fonksiyon sonucu garanti edilir |

#### 📋 Best Practices

**✅ Yapın:**
1. **Fonksiyon açıklamalarını net yazın** - LLM, `description` alanına bakarak karar verir
2. **Parametreleri detaylı tanımlayın** - Örnekler verin: `"örn: Istanbul, Ankara"`
3. **Hata yönetimi ekleyin** - Fonksiyonlar `try-except` ile korunmalı
4. **Required parametreleri belirtin** - Hangileri zorunlu, hangileri opsiyonel?
5. **Mock fonksiyonlarla başlayın** - Gerçek API entegrasyonundan önce test edin

**❌ Yapmayın:**
1. **Belirsiz açıklamalar** - "Bir şey yapar" yerine "İstanbul'daki sıcaklığı getirir"
2. **Çok fazla fonksiyon** - 10+ fonksiyon LLM'i karıştırır, gruplandırın
3. **Güvensiz eval()** - Kullanıcı girdisini direkt çalıştırmayın
4. **Sonsuz döngü riski** - `max_iterations` parametresi kullanın
5. **API key'leri kod içinde** - Environment variable kullanın

#### 🔄 Function Calling Akış Diyagramı

```
┌─────────────────────────────────────────────────────────────┐
│  1. Kullanıcı Sorusu: "İstanbul'da hava nasıl?"            │
└────────────────────┬────────────────────────────────────────┘
                     │
                     ▼
┌─────────────────────────────────────────────────────────────┐
│  2. LLM Analiz: "Hava durumu bilgisi lazım"                │
│     → Tool seçimi: get_current_weather()                    │
│     → Parametre çıkarma: {location: "Istanbul"}             │
└────────────────────┬────────────────────────────────────────┘
                     │
                     ▼
┌─────────────────────────────────────────────────────────────┐
│  3. Sistem: Fonksiyonu Çalıştır                             │
│     → Python: get_current_weather("Istanbul")               │
│     → Sonuç: {"temp": 18, "condition": "Parçalı bulutlu"}   │
└────────────────────┬────────────────────────────────────────┘
                     │
                     ▼
┌─────────────────────────────────────────────────────────────┐
│  4. LLM Final Yanıt: Fonksiyon sonucunu kullan             │
│     → "İstanbul'da hava 18 derece ve parçalı bulutlu."     │
└─────────────────────────────────────────────────────────────┘
```

####  Gerçek Dünya Kullanım Senaryoları

1. **Müşteri Destek Botu**
   - `search_knowledge_base()` - KB'de arama
   - `create_ticket()` - Destek talebi oluştur
   - `check_order_status()` - Sipariş durumu sorgula

2. **Veri Analiz Asistanı**
   - `query_database()` - SQL sorgusu çalıştır
   - `generate_chart()` - Görselleştirme yap
   - `calculate_stats()` - İstatistik hesapla

3. **Otomasyon Agent'ı**
   - `send_email()` - E-posta gönder
   - `schedule_meeting()` - Toplantı planla
   - `update_crm()` - CRM güncelle

#### 🔗 RAG + Function Calling = Enterprise AI

En güçlü kombinasyon:

```python
# Örnek: E-ticaret asistanı

tools = [
    search_product_catalog(),    # RAG ile ürün araması
    check_inventory(),            # Canlı stok kontrolü
    get_user_order_history(),    # Veritabanı sorgusu
    apply_discount(),             # Hesaplama
    create_order()                # Aksiyon
]
```

**Kullanıcı:** "Dün aldığım ayakkabıya uyan çorap var mı? Varsa %10 indirimli fiyatı ne olur?"

**Agent Adımları:**
1. `get_user_order_history()` → Ayakkabı modelini öğren
2. `search_product_catalog("ayakkabıya uyan çorap")` → RAG ile eşleşen ürünler
3. `check_inventory()` → Stok kontrolü
4. `apply_discount(price, 10)` → İndirimli fiyat hesapla
5. Final yanıt: "Evet. Siyah spor çorap stokta. Normal fiyat 50 TL, %10 indirimli 45 TL."

---

### 4.8 Alıştırma: Kendi Fonksiyonunuzu Ekleyin.

**Görev:** `convert_currency()` adında bir fonksiyon ekleyin.

**Fonksiyon Detayları:**
- **Adı:** `convert_currency`
- **Açıklama:** "Para birimi dönüşümü yapar"
- **Parametreler:**
  - `amount` (number, required): Miktar
  - `from_currency` (string, required): Kaynak para birimi (TRY, USD, EUR)
  - `to_currency` (string, required): Hedef para birimi

**İpucu:**
1. Önce Python fonksiyonunu yazın (simüle edilmiş kurlar kullanın)
2. Sonra `tools` listesine JSON schema ekleyin
3. `available_functions` dict'ine ekleyin
4. Test edin: "100 TRY kaç USD eder?"

**Beklenen Çıktı:**
```
Model: convert_currency fonksiyonunu çağırıyor
Parametreler: {amount: 100, from_currency: "TRY", to_currency: "USD"}
Sonuç: {"result": 3.57, "rate": 0.0357}
Final: "100 TRY, 3.57 USD eder (kur: 0.0357)"
```

---

** Tebrikler.** Artık LLM'lere araç kullanma yeteneği kazandırmayı öğrendiniz. Bu, otonom agent'lar oluşturmanın temel taşıdır.

---

## Hafta 9: Özet ve Anahtar Kavramlar

Bu hafta, LLM'leri gerçek dünya uygulamaları için güçlendiren üç ana tekniği öğrendik:

### 1️⃣ Fine-Tuning (İnce Ayar)

**Ne İşe Yarar:** Modelin davranışını, stilini, terminolojisini değiştirmek

**Ne Zaman Kullanılır:**
- Özel bir kişilik kazandırmak (örn: resmi/gayri resmi ton)
- Domain-specific terminoloji öğretmek (tıp, hukuk)
- Spesifik çıktı formatı sağlamak

**Dezavantajları:**
- Maliyetli (veri + GPU)
- Catastrophic forgetting riski
- Yeni gerçekler öğretmek için verimsiz

---

### 2️⃣ RAG (Retrieval-Augmented Generation)

**Ne İşe Yarar:** LLM'e harici bilgi tabanından "kopya çekme" yeteneği kazandırmak

**Nasıl Çalışır:**
1. **Offline:** Dökümanları embedding'e çevir → Vektör DB'ye kaydet
2. **Online:** Kullanıcı sorusu → Benzer dökümanları bul → LLM'e prompt olarak ver

**Avantajları:**
- Güncel bilgi (knowledge cutoff yok.)
- Güvenilir (kaynak gösterilebilir)
- Kolay güncelleme (yeni doküman ekle, model yeniden eğitilmez)

**Kullanım Alanları:**
- Şirket KB chatbot'ları
- Doküman Q&A sistemleri
- Araştırma asistanları

---

### 3️⃣ Function Calling (Fonksiyon Çağırma)

**Ne İşe Yarar:** LLM'e araçlar kullanma ve aksiyon alma yeteneği kazandırmak

**Nasıl Çalışır:**
1. Fonksiyonları JSON schema ile tanımla
2. LLM, hangi fonksiyonu hangi parametrelerle çağıracağına karar verir
3. Sistem fonksiyonu çalıştırır, sonucu LLM'e geri verir
4. LLM, sonucu kullanarak final yanıtı üretir

**Avantajları:**
- Kesin sonuçlar (hesaplama hataları yok)
- Canlı veri (API'ler, veritabanları)
- Gerçek aksiyonlar (e-posta gönderme, sipariş oluşturma)

**Kullanım Alanları:**
- Müşteri destek otomasyonu
- Veri analiz asistanları
- İş süreçleri otomasyonu

---

### 🔗 Güçlü Kombinasyon: RAG + Function Calling

En güçlü kombinasyon, ikisini birleştirmektir:

```python
# Örnek: Akıllı müşteri destek botu

tools = [
    search_knowledge_base(),    # RAG: KB'den ilgili makale bul
    get_user_data(),            # Function: CRM'den müşteri bilgisi çek
    check_order_status(),       # Function: Sipariş durumu sorgula
    create_support_ticket(),    # Function: Destek talebi oluştur
]
```

**Kullanıcı:** "Siparişim nerede ve iade politikanız nedir?"

**Agent:**
1. `check_order_status()` → "Kargoda, yarın teslim"
2. `search_knowledge_base("iade politikası")` → "14 gün içinde iade"
3. Final yanıt: Her iki soruyu da cevaplar.

---

### 📊 Teknik Karşılaştırma

| Özellik | Fine-Tuning | RAG | Function Calling |
|:--------|:------------|:----|:-----------------|
| **Amaç** | Davranış değiştirme | Bilgi genişletme | Aksiyon alma |
| **Maliyet** | Yüksek | Orta | Düşük |
| **Güncelleme** | Model yeniden eğit | Döküman ekle | Fonksiyon ekle |
| **Güvenilirlik** | Orta (halüsinasyon olabilir) | Yüksek (kaynak gösterir) | Çok yüksek (fonksiyon sonucu) |
| **Kullanım** | Stil/format/terminoloji | Bilgi sorguları | Hesaplama/API/aksiyon |

---

###  Hangi Tekniği Ne Zaman Kullanmalı?

**Senaryo 1: "Hukuk ofisimiz için dokümanları resmi dilde özetleyen asistan"**
→ **Fine-Tuning** (resmi dil için) + **RAG** (davalardan bilgi çekmek için)

**Senaryo 2: "Şirket politikalarını cevaplayan HR botu"**
→ **RAG** (politika dokümanlarından bilgi çekmek)

**Senaryo 3: "E-ticaret sipariş takip asistanı"**
→ **Function Calling** (sipariş durumu API'si) + **RAG** (SSS'ler için)

**Senaryo 4: "Veri analiz asistanı"**
→ **Function Calling** (veritabanı sorguları + hesaplamalar)

---

###  Sonraki Adımlar

Artık LLM'leri özelleştirmenin temel tekniklerini öğrendiniz. **Hafta 10**'da şunları göreceğiz:

1. **LangChain & LangGraph** - Agent framework'leri
2. **ReAct Pattern** - Reasoning + Acting
3. **Multi-Agent Systems** - Birden fazla agent'ın iş birliği
4. **LLMOps** - Production'da LLM yönetimi (monitoring, versioning, cost optimization)
5. **Prompt Versioning & Evaluation** - Prompt'ları nasıl test edip optimize ederiz

** Pratik Yapın:**
- Google AI Studio'da kendi fonksiyonlarınızı test edin
- RAG sisteminize yeni dökümanlar ekleyin
- Kendi use case'iniz için fonksiyon kombinasyonları deneyin

---

**🎓 Ek Kaynaklar:**

- **Google AI Studio:** https://aistudio.google.com/
- **LiteLLM Docs:** https://docs.litellm.ai/docs/completion/function_call
- **OpenAI Function Calling Guide:** https://platform.openai.com/docs/guides/function-calling
- **Anthropic Tool Use:** https://docs.anthropic.com/en/docs/build-with-claude/tool-use